# Import Packages

In [1]:
import pandas as pd
import boto3
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import cross_val_score
from decimal import Decimal
from urllib.parse import urlparse
from sagemaker_studio import Project

proj = Project()

In [2]:
proj.s3.root

's3://amazon-sagemaker-851209711676-us-east-1-c1223d975283/dzd_bv4ak0mc2hc15z/4yvsewnmdyc0pz/dev'

# Ingest Data

In [3]:
# Data File Path
file_name = 'joined_data.csv'
s3_folder = '/datalake/'
data_path = proj.s3.root + s3_folder + file_name

# Set up S3 client
s3 = boto3.client('s3')


# Function to read data
def read_csv_from_s3(s3_uri):
    # Parse the S3 URI
    parsed = urlparse(s3_uri)
    bucket = parsed.netloc
    key = parsed.path.lstrip('/')

    obj = s3.get_object(Bucket=bucket, Key=key)
    df = pd.read_csv(obj['Body'])

    return df

In [4]:
df = read_csv_from_s3(data_path)

In [5]:
# Review data

print("\nAll columns description:")
print(df.describe(include='all'))


All columns description:
                  timestamp        temp_f   rain_inches     windspeed  \
count              10905067  1.090507e+07  1.090507e+07  1.090507e+07   
unique                  756           NaN           NaN           NaN   
top     2016-01-01 01:00:00           NaN           NaN           NaN   
freq                  29005           NaN           NaN           NaN   
mean                    NaN  3.311438e+01  3.696746e+00  1.289984e+01   
std                     NaN  1.088655e+01  1.103445e+01  6.617347e+00   
min                     NaN -3.624145e+00  0.000000e+00  0.000000e+00   
25%                     NaN  2.671803e+01  0.000000e+00  8.839981e+00   
50%                     NaN  3.338451e+01  2.803760e-01  1.253439e+01   
75%                     NaN  3.968808e+01  2.976194e+00  1.668721e+01   
max                     NaN  8.747501e+01  1.638374e+02  3.955150e+01   

               rounded_hour  passenger_count  trip_distance  total_amount  \
count              1

# Data Clean Up and Transformation

In [6]:
# Data type conversions
# Check to see if there are any values in rain_inch column that can't be converted to float64

df['rain_inches'] = pd.to_numeric(df['rain_inches'], errors='coerce')
df['timestamp'] = pd.to_datetime(df['timestamp'], errors='coerce')
df['rounded_hour'] = pd.to_datetime(df['rounded_hour'], errors='coerce')

# drop any rows with a null
df.dropna(inplace=True)

# convert rain to binary, 0 = No, 1 = Yes
df['raining'] = np.where(df['rain_inches'] > 0, 1, 0)

# get day of week from ride time
df['day_of_week'] = df['timestamp'].dt.dayofweek

# Review Data

In [7]:
# Get num total rows
total_rows = df['total_amount'].count()

# Find number of rides with cost greater than $150
rows_over_150 = df['total_amount'][df['total_amount'] > 150].count()

# Proportion of rides in data set that cost greater than $150
proportion = rows_over_150 / total_rows
percentage = proportion * 100
print("Rides that cost greater thant $150")
print(f"Rows with total_amount > 150: {rows_over_150}")
print(f"Total rows: {total_rows}")
print(f"Percentage: {percentage:.2f}%")
print("\n")


# Find number of rides greater than 50 miles
rows_over_50 = df['trip_distance'][df['trip_distance'] > 50].count()

# Proportion of rides in data set that are greater than 50 miles
proportion = rows_over_50 / total_rows
percentage = proportion * 100
print("Rides greater than 50 miles")
print(f"Rows with trip_distance > 50: {rows_over_50}")
print(f"Total rows: {total_rows}")
print(f"Percentage: {percentage:.2f}%")
print("\n")

# Find number of rides longer than an hour
rows_over_hour = df['duration_minutes'][df['duration_minutes'] > 60].count()

# Proportion of rides in data set that are longer than an hour
proportion = rows_over_hour / total_rows
percentage = proportion * 100
print("Rides longer than 60 minutes")
print(f"Rows with trips ride_time > 60 minutes: {rows_over_hour}")
print(f"Total rows: {total_rows}")
print(f"Percentage: {percentage:.2f}%")
print("\n")

Rides that cost greater thant $150
Rows with total_amount > 150: 3595
Total rows: 10771735
Percentage: 0.03%


Rides greater than 50 miles
Rows with trip_distance > 50: 461
Total rows: 10771735
Percentage: 0.00%


Rides longer than 60 minutes
Rows with trips ride_time > 60 minutes: 74166
Total rows: 10771735
Percentage: 0.69%




In [8]:
# create df of all rows that contain rides that cost more than $150 or distance
# is greater than 50 miles or ride time is greater than 1 hour
# create df of all rows that contain rides where cost, distance, or ride time
# is less than or equal to zero
high_outliers_df = df[(df['total_amount'] > 150) | (df['trip_distance'] > 50) |
                      (df['duration_minutes'] > 60)]
low_outliers_df = df[(df['total_amount'] <= 0) | (df['trip_distance'] <= 0) |
                     (df['duration_minutes'] <= 0)]

In [9]:
# remove all rows that contain rides that cost more than $150 or distance is
# greater than 50 miles or ride time is greater than 1 hour
# remove all rows that contain rides where cost, distance, or ride time is less
# than or equal to zero
df_cleaned = df[(df['total_amount'] <= 150) & (df['trip_distance'] <= 50) &
                (df['duration_minutes'] <= 60) & (df['total_amount'] > 0) &
                (df['trip_distance'] > 0) & (df['duration_minutes'] > 0)]

In [10]:
# Reviewing the starting number of rows, number of rows that don't meet
# criteria, and remaining rows after removing rows that don't meet criteria

raw_row_count = df['timestamp'].count()
print(f"Number of raw rows: {raw_row_count}")

high_row_count = high_outliers_df['timestamp'].count()
print(f"Number of high outlier rows: {high_row_count}")

low_row_count = low_outliers_df['timestamp'].count()
print(f"Number of low outlier rows: {low_row_count}")

clean_row_count = df_cleaned['timestamp'].count()
print(f"Number of clean rows: {clean_row_count}")

Number of raw rows: 10771735
Number of high outlier rows: 76889
Number of low outlier rows: 65721
Number of clean rows: 10630427


In [11]:
# Look at impact of removing rows that dont' meet crtieria on average cost of ride
raw_avg_amt = df['total_amount'].mean()
high_out_avg_amt = high_outliers_df['total_amount'].mean()
low_out_avg_amt = low_outliers_df['total_amount'].mean()
rem_avg_amt = df_cleaned['total_amount'].mean()


print(f"Raw Avg Amount: {raw_avg_amt:.2f}")
print(f"High Outlier Avg Amount: {high_out_avg_amt:.2f}")
print(f"Low Outlier Avg Amount: {low_out_avg_amt:.2f}")
print(f"Clean Dataset Avg Amount: {rem_avg_amt:.2f}")

Raw Avg Amount: 15.64
High Outlier Avg Amount: 62.29
Low Outlier Avg Amount: 23.65
Clean Dataset Avg Amount: 15.27


In [12]:
# Look at impact of removing rows that dont' meet crtieria on average distancee of ride
raw_avg_dist = df['trip_distance'].mean()
high_out_avg_dist = high_outliers_df['trip_distance'].mean()
low_out_avg_dist = low_outliers_df['trip_distance'].mean()
rem_avg_dist = df_cleaned['trip_distance'].mean()

print(f"Raw Avg Distance: {raw_avg_dist:.2f}")
print(f"High Outlier Avg Distance: {high_out_avg_dist:.2f}")
print(f"Low Outlier Avg Distnace: {low_out_avg_dist:.2f}")
print(f"Dataset Avg Distance: {rem_avg_dist:.2f}")

Raw Avg Distance: 4.51
High Outlier Avg Distance: 240.77
Low Outlier Avg Distnace: 0.06
Dataset Avg Distance: 2.83


In [13]:
# Look at impact of removing rows that dont' meet crtieria on average ride time
raw_avg_time = df['duration_minutes'].mean()
high_out_avg_time = high_outliers_df['duration_minutes'].mean()
low_out_avg_time = low_outliers_df['duration_minutes'].mean()
rem_avg_time = df_cleaned['duration_minutes'].mean()

print(f"Raw Avg Distance: {raw_avg_time:.2f}")
print(f"High Outlier Avg Distance: {high_out_avg_time:.2f}")
print(f"Low Outlier Avg Distance: {low_out_avg_time:.2f}")
print(f"Dataset Avg Distance: {rem_avg_time:.2f}")

Raw Avg Distance: 15.26
High Outlier Avg Distance: 354.51
Low Outlier Avg Distance: 3.46
Dataset Avg Distance: 12.89


In [14]:
avg_by_day = (df_cleaned.groupby('day_of_week')[
              ['duration_minutes', 'trip_distance']]
              .mean()
              .round(2)
              .reset_index()
              .rename(columns={'duration_minutes': 'avg_duration',
                      'trip_distance': 'avg_distance'}))

print(avg_by_day)

   day_of_week  avg_duration  avg_distance
0            0         12.65          2.93
1            1         13.51          2.75
2            2         13.35          2.71
3            3         13.57          2.76
4            4         13.00          2.81
5            5         12.27          2.79
6            6         11.92          3.08


# Prediction

In [15]:
# calculating correlation between fare amount and potential features
input_feat = df_cleaned[['duration_minutes', 'raining', 'day_of_week',
                        'passenger_count', 'trip_distance', 'rain_inches',
                         'total_amount']]

# Get correlation of 'total_amount' with all other columns
correlations = input_feat.corr()['total_amount']

# If you want to exclude 'total_amount' itself from the result
correlations = correlations.drop('total_amount')

# Sort correlations from highest to lowest absolute value
correlations = correlations.abs().sort_values(ascending=False)

# Print the correlations
print(correlations.round(2))

trip_distance       0.94
duration_minutes    0.84
day_of_week         0.02
passenger_count     0.01
raining             0.00
rain_inches         0.00
Name: total_amount, dtype: float64


In [16]:
# Separate features (X) and target (y)
X = df_cleaned[['duration_minutes', 'passenger_count', 'trip_distance', 'raining']]
y = df_cleaned['total_amount']

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2,
                                                    random_state=42)

# Create and train the model
model = LinearRegression()
model.fit(X_train, y_train)

# Make predictions
y_pred = model.predict(X_test)

r_score = round(r2_score(y_test, y_pred), 3)
mse = round(np.sqrt(mean_squared_error(y_test, y_pred)), 3)

# Print results
print("\nModel Results:")
print(f"R² Score: {r_score}")
print(f"Root Mean Squared Error: {mse}")

# Print coefficients
coef_df = pd.DataFrame({
    'Feature': X.columns,
    'Coefficient': model.coef_
})
print("\nFeature Coefficients:")
print(coef_df)

# Print intercept
intercept = round(model.intercept_, 3)
print(f"\nIntercept: {intercept}")

# Feature importance (absolute values of coefficients)
coef_df['Abs_Coefficient'] = abs(coef_df['Coefficient'])
coef = coef_df.sort_values('Abs_Coefficient', ascending=False)
print("\nFeature Importance (based on absolute coefficients):")
print(coef)

# Example predictiona
actual_v = y_test.iloc[0]
pred_v = model.predict([X_test.iloc[0]])[0]
print("\nExample prediction for first test row:")
print(f"Actual value: {actual_v}")
print(f"Predicted value: {pred_v}")

# Optional: Cross-validation

cv_scores = cross_val_score(model, X, y, cv=5)
avg_cv = round(cv_scores.mean(), 3)
print(f"\nCross-validation scores: {cv_scores}")
print(f"Average CV score: {avg_cv}")


Model Results:
R² Score: 0.914
Root Mean Squared Error: 3.543

Feature Coefficients:
            Feature  Coefficient
0  duration_minutes     0.343172
1   passenger_count    -0.031637
2     trip_distance     2.607445
3           raining    -0.052013

Intercept: 3.54

Feature Importance (based on absolute coefficients):
            Feature  Coefficient  Abs_Coefficient
2     trip_distance     2.607445         2.607445
0  duration_minutes     0.343172         0.343172
3           raining    -0.052013         0.052013
1   passenger_count    -0.031637         0.031637

Example prediction for first test row:
Actual value: 6.8
Predicted value: 8.32727338477525

Cross-validation scores: [0.91683015 0.91857869 0.9171546  0.90769644 0.90997535]
Average CV score: 0.914


In [17]:
output = f"Model Results:\nR² Score: {r_score}\nRoot Mean Squared Error: {mse}\
         \n\nFeature Coefficients:\n{coef_df}\n\nIntercept: {intercept}\
         \n\nFeature Importance (based on absolute coefficients):\n{coef}\
         \n\nExample prediction for first test row:\nActual value:{actual_v}\
         \nPredicted value: {pred_v}\n\nCross-validation scores: {cv_scores}\
         \nAverage CV score: {avg_cv}"

In [18]:
print(output)

Model Results:
R² Score: 0.914
Root Mean Squared Error: 3.543         

Feature Coefficients:
            Feature  Coefficient  Abs_Coefficient
0  duration_minutes     0.343172         0.343172
1   passenger_count    -0.031637         0.031637
2     trip_distance     2.607445         2.607445
3           raining    -0.052013         0.052013

Intercept: 3.54         

Feature Importance (based on absolute coefficients):
            Feature  Coefficient  Abs_Coefficient
2     trip_distance     2.607445         2.607445
0  duration_minutes     0.343172         0.343172
3           raining    -0.052013         0.052013
1   passenger_count    -0.031637         0.031637         

Example prediction for first test row:
Actual value:6.8         
Predicted value: 8.32727338477525

Cross-validation scores: [0.91683015 0.91857869 0.9171546  0.90769644 0.90997535]         
Average CV score: 0.914


In [19]:
# Path to where data will be stored
file_name = 'results.txt'
s3_folder = '/datalake/output/'
data_path = proj.s3.root + s3_folder + file_name


# Create S3 client
s3_client = boto3.client('s3')


# Function to write the results to S3
def put_dataframe_to_s3_as_txt(s3_uri, txt):

    # Parse the S3 URI
    parsed = urlparse(s3_uri)
    bucket = parsed.netloc
    key = parsed.path.lstrip('/')

    # Upload to S3
    s3_client.put_object(
        Bucket=bucket,
        Key=key,
        Body=txt
    )

In [20]:
# Write result to S3
try:
    put_dataframe_to_s3_as_txt(data_path, output)
    print("DataFrame successfully uploaded as txt to S3")
except Exception as e:
    print(f"Error uploading DataFrame to S3: {str(e)}")

DataFrame successfully uploaded as txt to S3
